In [4]:
import os
import re
import pandas as pd
from datetime import datetime
import matplotlib.pyplot as plt
import numpy as np
from sklearn.metrics import (
    precision_score,
    accuracy_score,
    confusion_matrix,
    ConfusionMatrixDisplay,
    f1_score,
    classification_report,
)

In [5]:
from urllib.request import urlretrieve
def direct_load(fname):
    if not os.path.exists(f'{PATH}/{fname}'):
        urlretrieve(f'{REPO_URL}/{fname}', f'{PATH}/{fname}')
    df=pd.read_parquet(f'{PATH}/{fname}')
    return df


In [6]:
INSTRUMENT='GRAVITY'
RANGE='1m'
REPO_URL='https://huggingface.co/datasets/Paranal/parlogs-observations/resolve/main/data'
PATH='sample_data' # Convenient name to be Colab compatible

!mkdir -p $PATH

df_meta = direct_load(f'{INSTRUMENT}-{RANGE}-meta.parket')
df_inst = direct_load(f'{INSTRUMENT}-{RANGE}-traces.parket')
df_subs = direct_load(f'{INSTRUMENT}-{RANGE}-traces-SUBSYSTEMS.parket')
df_tele = direct_load(f'{INSTRUMENT}-{RANGE}-traces-TELESCOPES.parket')

Ya existe el subdirectorio o el archivo -p.
Error mientras se procesaba: -p.
Ya existe el subdirectorio o el archivo sample_data.
Error mientras se procesaba: sample_data.


In [7]:
df_meta.head()

START                     END  TIMEOUT   system  \
0 2019-04-02 02:26:35.908 2019-04-02 02:36:25.647    False  GRAVITY   
1 2019-04-02 02:36:25.647 2019-04-02 02:40:29.255    False  GRAVITY   
2 2019-04-02 02:40:47.528 2019-04-02 03:00:47.297    False  GRAVITY   
3 2019-04-02 03:00:52.001 2019-04-02 03:03:27.834    False  GRAVITY   
4 2019-04-02 03:03:31.388 2019-04-02 03:04:20.546    False  GRAVITY   

    procname              TPL_ID  ERROR  Aborted  SECONDS TEL  
0  bob_26244             GRAVITY   True    False    589.0  AT  
1  bob_26244  GRAVITY_single_acq   True    False    243.0  AT  
2  bob_25960  GRAVITY_single_acq  False     True   1199.0  AT  
3  bob_25960  GRAVITY_single_acq  False     True    155.0  AT  
4  bob_25960  GRAVITY_single_acq  False     True     49.0  AT

In [18]:
df_meta_errores = df_meta[(df_meta['ERROR']==True)]
print(f'Hay {len(df_meta_errores)} datos con ERROR=True')
df_meta_errores.head()

Hay 92 datos con ERROR=True


START                     END  TIMEOUT   system  \
0  2019-04-02 02:26:35.908 2019-04-02 02:36:25.647    False  GRAVITY   
1  2019-04-02 02:36:25.647 2019-04-02 02:40:29.255    False  GRAVITY   
5  2019-04-02 03:04:32.278 2019-04-02 03:09:03.371    False  GRAVITY   
6  2019-04-02 03:10:14.125 2019-04-02 03:10:27.129    False  GRAVITY   
13 2019-04-02 04:59:14.976 2019-04-02 05:15:59.923    False  GRAVITY   

     procname              TPL_ID  ERROR  Aborted  SECONDS TEL  
0   bob_26244             GRAVITY   True    False    589.0  AT  
1   bob_26244  GRAVITY_single_acq   True    False    243.0  AT  
5   bob_25960  GRAVITY_single_acq   True    False    271.0  AT  
6   bob_25960  GRAVITY_single_acq   True    False     13.0  AT  
13  bob_15976    GRAVITY_dual_acq   True    False   1004.0  AT

In [20]:
df_inst.head()

@timestamp   system hostname loghost logtype envname  \
0 2019-04-02 02:26:35.908  GRAVITY      wgv     wgv     LOG     wgv   
1 2019-04-02 02:26:35.908  GRAVITY      wgv     wgv     LOG     wgv   
2 2019-04-02 02:26:36.000  GRAVITY      wgv     wgv    FLOG     wgv   
3 2019-04-02 02:26:36.000  GRAVITY      wgv     wgv    FLOG     wgv   
4 2019-04-02 02:26:36.000  GRAVITY      wgv     wgv    FLOG     wgv   

     procname  procid module keywname keywvalue keywmask  \
0   bob_26244      87    seq                               
1   bob_26244      87    seq                               
2  logManager       0                                wgv   
3  logManager       0                                wgv   
4  logManager       0                                wgv   

                                             logtext  trace_id  
0  GRAVITY_single_acq -- GRAVITY Single Mode Acqu...         0  
1        Started at 2019-04-02T02:26:35 (underlined)         0  
2                   COMMENT  FTOPT LOOP (DB) STOPPED         0  
3  COMMENT  LONGITUDINAL PUPIL POSITION LOOP STOPPED         0  
4            COMMENT  FIELD IMAGER LOOP (DB) STOPPED         0

In [21]:
def listas_logtext(df):
    #Aca guardo los valores de las trace_id
    traces = df['trace_id'].unique()
    listas_log=[]
    for traza in traces:
        trace = df[df['trace_id']== traza]
        log_text_trace_id = (list(trace['logtext'])) #el set es porque deben haber logs que se repiten entonces saco las repeticiones
        listas_log.append(log_text_trace_id)
    
    return listas_log

trace_log= listas_logtext(df_inst)

In [24]:
print('Logs del trace_id:0')
print(trace_log[0])

Logs del trace_id:0
['GRAVITY_single_acq -- GRAVITY Single Mode Acquisition (yellow)', 'Started at 2019-04-02T02:26:35 (underlined)', 'COMMENT  FTOPT LOOP (DB) STOPPED', 'COMMENT  LONGITUDINAL PUPIL POSITION LOOP STOPPED', 'COMMENT  FIELD IMAGER LOOP (DB) STOPPED', 'COMMENT  LATERAL PUPIL POSITION LOOP STOPPED', "COU GS MAG = '4.74'", "COU AG OBJCNT = 'F'", "DEL REF NAME = '1'", "COU AG ALPHA = '000000.000'", "COU AG GSSOURCE = 'SCIENCE'", "COU AG OPTIMIZE = 'F'", "DEL REF OPL = '250'", "COU GS WAVELEN = '650.0'", "DEL REF MODE = 'AUTO'", "COU AG PMD = '0.0'", "COU AG TYPE = 'DEFAULT'", "COU AG START = 'F'", "COU AG DELTA = '000000.000'", "COU AG PMA = '0.0'", "COU GS FWHM = '0.0'", "DET2 NDIT SKY = '1'", "INS ACQ FILTER = 'AUTO'", "DET1 DIT = '0.7'", "DET2 DIT = '0.3'", "INS SPEC RES = 'MED'", "INS STSOFFANG = '90'", "INS SPEC POL = 'IN'", "INS FT POL = 'IN'", "SEQ FI HMAG = '1.03'", "SEQ FRINGETRACK = 'T'", "SEQ FI WIN = '110.0'", "SEQ ALIGN = 'F'", "SEQ INS SOBJ MAG = '1.1'", "SEQ I

In [25]:
# Crear el nuevo DataFrame df_meta de MATISSE 

df_nuevo_meta =  pd.DataFrame(df_inst['trace_id'].unique())
df_nuevo_meta.columns = ['trace_id']
df_nuevo_meta['trace_logs'] = trace_log
df_nuevo_meta['ERROR'] = df_meta['ERROR'].to_list()
df_nuevo_meta

trace_id                                         trace_logs  ERROR
0           0  [GRAVITY_single_acq -- GRAVITY Single Mode Acq...   True
1           1  [Started at 2019-04-02T02:36:25 (underlined), ...   True
2           2  [Started at 2019-04-02T02:40:47 (underlined), ...  False
3           3  [GRAVITY_single_acq -- GRAVITY Single Mode Acq...  False
4           4  [Started at 2019-04-02T03:03:31 (underlined), ...  False
..        ...                                                ...    ...
763       763  [Started at 2019-04-30T22:13:55 (underlined), ...  False
764       764  [Started at 2019-04-30T22:17:55 (underlined), ...  False
765       765  [GRAVITY_gen_tec_AcqFibB -- Calibrate AcqCam_F...  False
766       766  [Started at 2019-04-30T22:32:28 (underlined), ...  False
767       767  [Started at 2019-04-30T22:34:02 (underlined), ...  False

[768 rows x 3 columns]

In [27]:
df_nuevo_meta[df_nuevo_meta['ERROR']==True]

trace_id                                         trace_logs  ERROR
0           0  [GRAVITY_single_acq -- GRAVITY Single Mode Acq...   True
1           1  [Started at 2019-04-02T02:36:25 (underlined), ...   True
5           5  [Started at 2019-04-02T03:04:32 (underlined), ...   True
6           6  [Started at 2019-04-02T03:10:14 (underlined), ...   True
13         13  [GRAVITY_dual_acq -- GRAVITY Dual Mode Acquisi...   True
..        ...                                                ...    ...
727       727  [GRAVITY_dual_acq -- GRAVITY Dual Mode Acquisi...   True
731       731  [GRAVITY_single_obs_exp -- Single Field Scienc...   True
732       732  [Started at 2019-04-29T00:20:26 (underlined), ...   True
754       754  [GRAVITY_gen_tec_checkMetZero -- Check Metrolo...   True
758       758  [Started at 2019-04-30T21:22:57 (underlined), ...   True

[92 rows x 3 columns]

In [28]:
trazas_error = (df_nuevo_meta[df_nuevo_meta['ERROR']==True]['trace_logs']).to_list()
trazas_error

[['GRAVITY_single_acq -- GRAVITY Single Mode Acquisition (yellow)',
  'Started at 2019-04-02T02:26:35 (underlined)',
  'COMMENT  FTOPT LOOP (DB) STOPPED',
  'COMMENT  LONGITUDINAL PUPIL POSITION LOOP STOPPED',
  'COMMENT  FIELD IMAGER LOOP (DB) STOPPED',
  'COMMENT  LATERAL PUPIL POSITION LOOP STOPPED',
  "COU GS MAG = '4.74'",
  "COU AG OBJCNT = 'F'",
  "DEL REF NAME = '1'",
  "COU AG ALPHA = '000000.000'",
  "COU AG GSSOURCE = 'SCIENCE'",
  "COU AG OPTIMIZE = 'F'",
  "DEL REF OPL = '250'",
  "COU GS WAVELEN = '650.0'",
  "DEL REF MODE = 'AUTO'",
  "COU AG PMD = '0.0'",
  "COU AG TYPE = 'DEFAULT'",
  "COU AG START = 'F'",
  "COU AG DELTA = '000000.000'",
  "COU AG PMA = '0.0'",
  "COU GS FWHM = '0.0'",
  "DET2 NDIT SKY = '1'",
  "INS ACQ FILTER = 'AUTO'",
  "DET1 DIT = '0.7'",
  "DET2 DIT = '0.3'",
  "INS SPEC RES = 'MED'",
  "INS STSOFFANG = '90'",
  "INS SPEC POL = 'IN'",
  "INS FT POL = 'IN'",
  "SEQ FI HMAG = '1.03'",
  "SEQ FRINGETRACK = 'T'",
  "SEQ FI WIN = '110.0'",
  "SEQ ALI

In [29]:
print(f'Hay {len(trazas_error)} trazas que tienen error')
print(f'La primera traza con error tiene una lista de log_text con {len(trazas_error[0])} logs')
print(trazas_error[0])

Hay 92 trazas que tienen error
La primera traza con error tiene una lista de log_text con 2073 logs
['GRAVITY_single_acq -- GRAVITY Single Mode Acquisition (yellow)', 'Started at 2019-04-02T02:26:35 (underlined)', 'COMMENT  FTOPT LOOP (DB) STOPPED', 'COMMENT  LONGITUDINAL PUPIL POSITION LOOP STOPPED', 'COMMENT  FIELD IMAGER LOOP (DB) STOPPED', 'COMMENT  LATERAL PUPIL POSITION LOOP STOPPED', "COU GS MAG = '4.74'", "COU AG OBJCNT = 'F'", "DEL REF NAME = '1'", "COU AG ALPHA = '000000.000'", "COU AG GSSOURCE = 'SCIENCE'", "COU AG OPTIMIZE = 'F'", "DEL REF OPL = '250'", "COU GS WAVELEN = '650.0'", "DEL REF MODE = 'AUTO'", "COU AG PMD = '0.0'", "COU AG TYPE = 'DEFAULT'", "COU AG START = 'F'", "COU AG DELTA = '000000.000'", "COU AG PMA = '0.0'", "COU GS FWHM = '0.0'", "DET2 NDIT SKY = '1'", "INS ACQ FILTER = 'AUTO'", "DET1 DIT = '0.7'", "DET2 DIT = '0.3'", "INS SPEC RES = 'MED'", "INS STSOFFANG = '90'", "INS SPEC POL = 'IN'", "INS FT POL = 'IN'", "SEQ FI HMAG = '1.03'", "SEQ FRINGETRACK = 'T'